# Semblance Calculation:

This module contains the scripts to perform the semblance calculation for input and output checkerboard. The input checkerboards are created by multipying three sin functions in three directions. The output checkerboards are obtained from the LOTOS code. The semblance is calculated following Kiser et al. 2016 after averaging over neighbouring nodes.The step by step process is shown below:

## 1. Import Modules

In [125]:
import numpy as np
import pygmt
import pandas as pd
from scipy.interpolate import interp1d
from functools import reduce
import matplotlib.pyplot as plt
from math import *

## 2. Run the shell script to obtain the model file

In [31]:
%%sh
home="/Users/sankha/Desktop/research/southern_puna/lotos"

cd $home/PROGRAMS/2_INVERS_3D/8n_3D_model
./mod_3D.exe>$home/checkerboard_test/check20_20_8/dv3D_synth001.dat


cp $home/DATA/PUNASLP1/SYNTH001/data/refmod.dat $home/checkerboard_test/check20_20_8/

## 3. Clean up the input file and refmod file from text before running further codes.

## 4. Interpolate through 1D model and calculate percentage change for each anomaly:

Run the script twice as the file is not written completely on the first run for some reason.

In [1]:
#Add the absolute velocity with the anomaly using refmod.dat

fo=open("../check20_20_8/dv3D_synth001_r1_neu_abs_p.dat",'w') #output file
df_mod=pd.read_csv("../check20_20_8/refmod.dat", sep="\s+",header=None) #reference 1D model file

#Interpolate either P or S velocity
f1=interp1d(df_mod[0],df_mod[1])

#Check Z range in major_param.dat
dzt=np.arange(-4,21,1)

#Interpolate at Z values
dvt=f1(dzt)

#print((dzt,dvt))

df_obt=pd.read_csv("../check20_20_8/dv3D_synth001_r1.dat",sep="\s+",header=None)

#Adds a column of absolute velocity and change in velocity in percent.
k=0
for i in range(len(df_obt[0])):
    
    if df_obt[0][i]==1: #P or S
        print(df_obt[0][i],df_obt[1][i],df_obt[2][i],df_obt[3][i],df_obt[4][i],dvt[k],(df_obt[4][i]/dvt[k])*100,file=fo)
        k=k+1
        if k%25==0: #be careful for each file
            k=0

FileNotFoundError: [Errno 2] No such file or directory: '../check20_20_8/dv3D_synth001_r1_neu_abs_p.dat'

## 5. Transform nodes to coordinates (optional)

In [156]:
#Nodes to coordinates for velocity model
lat0=-26.7
lon0=-67.1
dep0=-4.0
df_real = pd.read_csv("../check20_20_8/dv3D_synth001_r1_neu_abs_p.dat",sep="\s+",header=None)
#print(df_real)
a1=4.0/110.574
a2=4.0/(111.320*cos(lat0*pi/180))
lonlist=round((lon0+(df_real[1]-36)*a2),4)
latlist=round((lat0+(df_real[2]-36)*a1),4)
deplist=(dep0+df_real[3]-1)

# initialize data of lists.
data = {0: lonlist,1: latlist,2:deplist,3:df_real[4],4:df_real[5],5:df_real[6]}

# Create DataFrame
df = pd.DataFrame(data)
print(df)
df.to_csv("../check20_20_8/dv3D_synth001_r1_neu_abs_coord_p.dat",sep=" ",index=False,header=None)


              0        1     2    3      4    5
0      -68.5077 -27.9661  -4.0  0.0  5.732  0.0
1      -68.5077 -27.9661  -3.0  0.0  5.744  0.0
2      -68.5077 -27.9661  -2.0  0.0  5.756  0.0
3      -68.5077 -27.9661  -1.0  0.0  5.768  0.0
4      -68.5077 -27.9661   0.0  0.0  5.780  0.0
...         ...      ...   ...  ...    ...  ...
126020 -65.6923 -25.4339  16.0  0.0  5.952  0.0
126021 -65.6923 -25.4339  17.0  0.0  5.984  0.0
126022 -65.6923 -25.4339  18.0  0.0  6.016  0.0
126023 -65.6923 -25.4339  19.0  0.0  6.048  0.0
126024 -65.6923 -25.4339  20.0  0.0  6.080  0.0

[126025 rows x 6 columns]


## 6. Generate the input checkerboard pattern:

We need to do this only for P. For S models, the checkerboard remains same.

In [95]:
d2r=pi/180.  #degree to radian
amp=10.0    #Checkerboard anomaly amplitude

#checkerboard size
checksize_hor=20 
checksize_vert=8
#nodespace
nph=4 
npv=1 
#Node limits
horlimit=[-140,140]  
vertlimit=[-4,20]
#Checkerboard limits
checklimit_x=[-120,120]
checklimit_y=[-120,120]
checklimit_z=[-3,19]
#Period of sin function
tph=2.0*checksize_hor/nph
tpv=2.0*checksize_vert/npv
#Number of nodes
hn=1+(horlimit[1]-horlimit[0])/nph  
vn=1+(vertlimit[1]-vertlimit[0])       
x=np.arange(1,hn+1,1)
y=np.arange(1,hn+1,1)
z=np.arange(1,vn+1,1)
#Nodes where no checkerboards are placed
nochkx = [abs(horlimit[0]-checklimit_x[0])/nph,abs(horlimit[1]-checklimit_x[1])/nph]
nochky = [abs(horlimit[0]-checklimit_y[0])/nph,abs(horlimit[1]-checklimit_y[1])/nph]
nochkz = [abs(vertlimit[0]-checklimit_z[0])/npv,abs(vertlimit[1]-checklimit_z[1])/npv]
xmin=(1+nochkx[0])
ymin=(1+nochky[0])
zmin=(1+nochkz[0])
#print(xmin,(hn-nochkx[1]),ymin,(hn-nochky[1]),zmin,tph,tpv)

fo=open("../check20_20_8/dv3D_synth001_input_intm_p.dat",'w')

for i in x:
    for j in y:
        for k in z:
            if i>=xmin and i<=(hn-nochkx[1]) and j>=ymin and j<=(hn-nochky[1]) and k>=zmin:
                dv=(np.sin(2*pi*(i-xmin)/tph)) * (np.sin(2*pi*(j-ymin)/tph)) * (np.sin(2*pi*(k-zmin)/tpv)) *amp
            else:
                dv=0
            print(i,j,k,round(dv,4),file=fo)
            
#Same sorting as the output model
df=pd.read_csv("../check20_20_8/dv3D_synth001_input_intm_p.dat",sep="\s+",header=None)
df2=df.sort_values(by=[0, 1])
print(df2)
df2.to_csv("../check20_20_8/dv3D_synth001_r7_zup_input_p.dat",sep=" ",index=False,header=None)            

           0     1   2    3
0        1.0   1.0   1  0.0
1        1.0   1.0   2  0.0
2        1.0   1.0   3  0.0
3        1.0   1.0   4  0.0
4        1.0   1.0   5  0.0
...      ...   ...  ..  ...
126020  71.0  71.0  21  0.0
126021  71.0  71.0  22  0.0
126022  71.0  71.0  23  0.0
126023  71.0  71.0  24  0.0
126024  71.0  71.0  25  0.0

[126025 rows x 4 columns]


In [52]:
#Nodes to coordinates for semblance
lat0=-26.7
lon0=-67.1
dep0=-4.0

df_sem = pd.read_csv("../check20_20_8/dv3D_synth001_r1_neu_input_p.dat",sep="\s+",header=None)
a1=4.0/110.574
a2=4.0/(111.320*cos(lat0*pi/180))

lonlist=round((lon0+(df_sem[0]-36)*a2),4)
latlist=round((lat0+(df_sem[1]-36)*a1),4)
deplist=(dep0+df_sem[2]-1)

# initialize data of lists.
data = {0: lonlist,1: latlist,2:deplist,3:df_sem[3]}  
# Create DataFrame
df = pd.DataFrame(data)
print(df)
df.to_csv("../check20_20_8/dv3D_synth001_r1_neu_input_coord_p.dat",sep=" ",index=False,header=None)

              0        1     2    3
0      -68.5077 -27.9661  -4.0  0.0
1      -68.5077 -27.9661  -3.0  0.0
2      -68.5077 -27.9661  -2.0  0.0
3      -68.5077 -27.9661  -1.0  0.0
4      -68.5077 -27.9661   0.0  0.0
...         ...      ...   ...  ...
126020 -65.6923 -25.4339  16.0  0.0
126021 -65.6923 -25.4339  17.0  0.0
126022 -65.6923 -25.4339  18.0  0.0
126023 -65.6923 -25.4339  19.0  0.0
126024 -65.6923 -25.4339  20.0  0.0

[126025 rows x 4 columns]


## 7. Calculate the semblance averaging over nearby nodes

In [160]:
#Semblance on the nodes with neighbours
df_in=pd.read_csv("../check20_20_8/dv3D_synth001_r1_neu_input_p.dat",sep="\s+",header=None)
print(df_in.shape)
df_out=pd.read_csv("../check20_20_8/dv3D_synth001_r1_neu_abs_p.dat",sep="\s+",header=None)
print(df_out.shape)

fo=open("../check20_20_8/semblance_synth001_avgnd_r1_neu_p.dat",'w')
sem=[]
for j in range(len(df_in[0])):
    
    #Find distances from all values
    k1=abs(df_in[0]-df_in[0][j])
    k2=abs(df_in[1]-df_in[1][j])
    k3=abs(df_in[2]-df_in[2][j])
    
    idx=reduce(np.intersect1d,(np.where(k1<=1),np.where(k2<=1),np.where(k3<=1 )))
    
    #Anomaly values at those indices
    PT=(df_in[3][idx])
    PR=(df_out[6][idx])

    #Calculate the semblance
    ll=(np.sum((PT+PR)**2))
    dl=(2*np.sum(PT**2+PR**2))    
    if dl==0:
        s=0.5
    else:
        s=ll/ dl  #Semblance formula
    sem.append(s)        
    print(int(df_in[0][j]),int(df_in[1][j]),int(df_in[2][j]),df_in[3][j],df_out[6][j],s)
    print(int(df_in[0][j]),int(df_in[1][j]),int(df_in[2][j]),df_in[3][j],df_out[6][j],s,file=fo)

(126025, 4)
(126025, 7)
1 1 1 0.0 0.0 0.5
1 1 2 0.0 0.0 0.5
1 1 3 0.0 0.0 0.5
1 1 4 0.0 0.0 0.5
1 1 5 0.0 0.0 0.5
1 1 6 0.0 0.0 0.5
1 1 7 0.0 0.0 0.5
1 1 8 0.0 0.0 0.5
1 1 9 0.0 0.0 0.5
1 1 10 0.0 0.0 0.5
1 1 11 0.0 0.0 0.5
1 1 12 0.0 0.0 0.5
1 1 13 0.0 0.0 0.5
1 1 14 0.0 0.0 0.5
1 1 15 0.0 0.0 0.5
1 1 16 0.0 0.0 0.5
1 1 17 0.0 0.0 0.5
1 1 18 0.0 0.0 0.5
1 1 19 0.0 0.0 0.5
1 1 20 0.0 0.0 0.5
1 1 21 0.0 0.0 0.5
1 1 22 0.0 0.0 0.5
1 1 23 0.0 0.0 0.5
1 1 24 0.0 0.0 0.5
1 1 25 0.0 0.0 0.5
1 2 1 0.0 0.0 0.5
1 2 2 0.0 0.0 0.5
1 2 3 0.0 0.0 0.5
1 2 4 0.0 0.0 0.5
1 2 5 0.0 0.0 0.5
1 2 6 0.0 0.0 0.5
1 2 7 0.0 0.0 0.5
1 2 8 0.0 0.0 0.5
1 2 9 0.0 0.0 0.5
1 2 10 0.0 0.0 0.5
1 2 11 0.0 0.0 0.5
1 2 12 0.0 0.0 0.5
1 2 13 0.0 0.0 0.5
1 2 14 0.0 0.0 0.5
1 2 15 0.0 0.0 0.5
1 2 16 0.0 0.0 0.5
1 2 17 0.0 0.0 0.5
1 2 18 0.0 0.0 0.5
1 2 19 0.0 0.0 0.5
1 2 20 0.0 0.0 0.5
1 2 21 0.0 0.0 0.5
1 2 22 0.0 0.0 0.5
1 2 23 0.0 0.0 0.5
1 2 24 0.0 0.0 0.5
1 2 25 0.0 0.0 0.5
1 3 1 0.0 0.0 0.5
1 3 2 0.0 0.0 0.5
1 3 3 0.

1 18 1 0.0 0.0 0.5
1 18 2 0.0 -0.0122757818593314 0.5
1 18 3 0.0 -0.0248611028492008 0.5
1 18 4 0.0 -0.034574773404993 0.5
1 18 5 0.0 -0.0491448610726643 0.5
1 18 6 0.0 -0.042965932912844 0.5
1 18 7 0.0 -0.0114849724857468 0.5
1 18 8 0.0 0.0247838498299319 0.5
1 18 9 0.0 0.0474003667988668 0.5
1 18 10 0.0 0.0257451310872027 0.5
1 18 11 0.0 0.0157553610865874 0.5
1 18 12 0.0 0.0105582635803167 0.5
1 18 13 0.0 0.0051834971735443 0.5
1 18 14 0.0 -0.0029748625762711 0.5
1 18 15 0.0 -0.008376849751693 0.5
1 18 16 0.0 -0.0082741025140924 0.5
1 18 17 0.0 0.1017983005067567 0.5
1 18 18 0.0 0.3073922972972973 0.5
1 18 19 0.0 0.0 0.5
1 18 20 0.0 0.0 0.5
1 18 21 0.0 0.0 0.5
1 18 22 0.0 0.0 0.5
1 18 23 0.0 0.0 0.5
1 18 24 0.0 0.0 0.5
1 18 25 0.0 0.0 0.5
1 19 1 0.0 0.0 0.5
1 19 2 0.0 0.0894977078690807 0.5
1 19 3 0.0 0.180174351980542 0.5
1 19 4 0.0 0.2666140950069348 0.5
1 19 5 0.0 0.3411034671280277 0.5
1 19 6 0.0 0.4085734661697248 0.5
1 19 7 0.0 0.4731795239452679 0.5
1 19 8 0.0 0.5405417125850

1 28 25 0.0 0.0 0.5
1 29 1 0.0 0.0 0.5
1 29 2 0.0 -0.0219832560933147 0.5
1 29 3 0.0 0.0129856720639332 0.5
1 29 4 0.0 -0.087987507628294 0.5
1 29 5 0.0 -0.2442970138408304 0.5
1 29 6 0.0 -0.3396749913990826 0.5
1 29 7 0.0 -0.3447742474344356 0.5
1 29 8 0.0 -0.33231525 0.5
1 29 9 0.0 -0.325531811898017 0.5
1 29 10 0.0 -0.3158974773499433 0.5
1 29 11 0.0 -0.2895988505942275 0.5
1 29 12 0.0 -0.2748471872171946 0.5
1 29 13 0.0 -0.2604968513284341 0.5
1 29 14 0.0 -0.2461627152542373 0.5
1 29 15 0.0 -0.2304095773137697 0.5
1 29 16 0.0 0.0 0.5
1 29 17 0.0 0.0 0.5
1 29 18 0.0 0.0 0.5
1 29 19 0.0 0.0 0.5
1 29 20 0.0 0.0 0.5
1 29 21 0.0 0.0 0.5
1 29 22 0.0 0.0 0.5
1 29 23 0.0 0.0 0.5
1 29 24 0.0 0.0 0.5
1 29 25 0.0 0.0 0.5
1 30 1 0.0 0.0 0.5
1 30 2 0.0 -0.1521688344359331 0.5
1 30 3 0.0 -0.2245126025017373 0.5
1 30 4 0.0 -0.3277411338418863 0.5
1 30 5 0.0 -0.44048576816609 0.5
1 30 6 0.0 -0.517443431766055 0.5
1 30 7 0.0 -0.5043500096921323 0.5
1 30 8 0.0 -0.4784114421768707 0.5
1 30 9 0.0 -0.4

1 41 6 0.0 0.0 0.5
1 41 7 0.0 0.0 0.5
1 41 8 0.0 0.0 0.5
1 41 9 0.0 0.0 0.5
1 41 10 0.0 0.0 0.5
1 41 11 0.0 0.0 0.5
1 41 12 0.0 0.0 0.5
1 41 13 0.0 0.0 0.5
1 41 14 0.0 0.0 0.5
1 41 15 0.0 0.0 0.5
1 41 16 0.0 0.0 0.5
1 41 17 0.0 0.0 0.5
1 41 18 0.0 0.0 0.5
1 41 19 0.0 0.0 0.5
1 41 20 0.0 0.0 0.5
1 41 21 0.0 0.0 0.5
1 41 22 0.0 0.0 0.5
1 41 23 0.0 0.0 0.5
1 41 24 0.0 0.0 0.5
1 41 25 0.0 0.0 0.5
1 42 1 0.0 0.0 0.5
1 42 2 0.0 0.0 0.5
1 42 3 0.0 0.0 0.5
1 42 4 0.0 0.0 0.5
1 42 5 0.0 0.0 0.5
1 42 6 0.0 0.0 0.5
1 42 7 0.0 0.0 0.5
1 42 8 0.0 0.0 0.5
1 42 9 0.0 0.0 0.5
1 42 10 0.0 0.0 0.5
1 42 11 0.0 0.0 0.5
1 42 12 0.0 0.0 0.5
1 42 13 0.0 0.0 0.5
1 42 14 0.0 0.0 0.5
1 42 15 0.0 0.0 0.5
1 42 16 0.0 0.0 0.5
1 42 17 0.0 0.0 0.5
1 42 18 0.0 0.0 0.5
1 42 19 0.0 0.0 0.5
1 42 20 0.0 0.0 0.5
1 42 21 0.0 0.0 0.5
1 42 22 0.0 0.0 0.5
1 42 23 0.0 0.0 0.5
1 42 24 0.0 0.0 0.5
1 42 25 0.0 0.0 0.5
1 43 1 0.0 0.0 0.5
1 43 2 0.0 0.0 0.5
1 43 3 0.0 0.0 0.5
1 43 4 0.0 0.0 0.5
1 43 5 0.0 0.0 0.5
1 43 6 0.0 0.0 0.5

1 58 10 0.0 0.0 0.5
1 58 11 0.0 0.0 0.5
1 58 12 0.0 0.0 0.5
1 58 13 0.0 0.0 0.5
1 58 14 0.0 0.0 0.5
1 58 15 0.0 0.0 0.5
1 58 16 0.0 0.0 0.5
1 58 17 0.0 0.0 0.5
1 58 18 0.0 0.0 0.5
1 58 19 0.0 0.0 0.5
1 58 20 0.0 0.0 0.5
1 58 21 0.0 0.0 0.5
1 58 22 0.0 0.0 0.5
1 58 23 0.0 0.0 0.5
1 58 24 0.0 0.0 0.5
1 58 25 0.0 0.0 0.5
1 59 1 0.0 0.0 0.5
1 59 2 0.0 0.0 0.5
1 59 3 0.0 0.0 0.5
1 59 4 0.0 0.0 0.5
1 59 5 0.0 0.0 0.5
1 59 6 0.0 0.0 0.5
1 59 7 0.0 0.0 0.5
1 59 8 0.0 0.0 0.5
1 59 9 0.0 0.0 0.5
1 59 10 0.0 0.0 0.5
1 59 11 0.0 0.0 0.5
1 59 12 0.0 0.0 0.5
1 59 13 0.0 0.0 0.5
1 59 14 0.0 0.0 0.5
1 59 15 0.0 0.0 0.5
1 59 16 0.0 0.0 0.5
1 59 17 0.0 0.0 0.5
1 59 18 0.0 0.0 0.5
1 59 19 0.0 0.0 0.5
1 59 20 0.0 0.0 0.5
1 59 21 0.0 0.0 0.5
1 59 22 0.0 0.0 0.5
1 59 23 0.0 0.0 0.5
1 59 24 0.0 0.0 0.5
1 59 25 0.0 0.0 0.5
1 60 1 0.0 0.0 0.5
1 60 2 0.0 0.0 0.5
1 60 3 0.0 0.0 0.5
1 60 4 0.0 0.0 0.5
1 60 5 0.0 0.0 0.5
1 60 6 0.0 0.0 0.5
1 60 7 0.0 0.0 0.5
1 60 8 0.0 0.0 0.5
1 60 9 0.0 0.0 0.5
1 60 10 0.0 0.0 0.

...

70 66 15 0.0 0.0 0.5
70 66 16 0.0 0.0 0.5
70 66 17 0.0 0.0 0.5
70 66 18 0.0 0.0 0.5
70 66 19 0.0 0.0 0.5
70 66 20 0.0 0.0 0.5
70 66 21 0.0 0.0 0.5
70 66 22 0.0 0.0 0.5
70 66 23 0.0 0.0 0.5
70 66 24 0.0 0.0 0.5
70 66 25 0.0 0.0 0.5
70 67 1 0.0 0.0 0.5
70 67 2 0.0 0.0 0.5
70 67 3 0.0 0.0 0.5
70 67 4 0.0 0.0 0.5
70 67 5 0.0 0.0 0.5
70 67 6 0.0 0.0 0.5
70 67 7 0.0 0.0 0.5
70 67 8 0.0 0.0 0.5
70 67 9 0.0 0.0 0.5
70 67 10 0.0 0.0 0.5
70 67 11 0.0 0.0 0.5
70 67 12 0.0 0.0 0.5
70 67 13 0.0 0.0 0.5
70 67 14 0.0 0.0 0.5
70 67 15 0.0 0.0 0.5
70 67 16 0.0 0.0 0.5
70 67 17 0.0 0.0 0.5
70 67 18 0.0 0.0 0.5
70 67 19 0.0 0.0 0.5
70 67 20 0.0 0.0 0.5
70 67 21 0.0 0.0 0.5
70 67 22 0.0 0.0 0.5
70 67 23 0.0 0.0 0.5
70 67 24 0.0 0.0 0.5
70 67 25 0.0 0.0 0.5
70 68 1 0.0 0.0 0.5
70 68 2 0.0 0.0 0.5
70 68 3 0.0 0.0 0.5
70 68 4 0.0 0.0 0.5
70 68 5 0.0 0.0 0.5
70 68 6 0.0 0.0 0.5
70 68 7 0.0 0.0 0.5
70 68 8 0.0 0.0 0.5
70 68 9 0.0 0.0 0.5
70 68 10 0.0 0.0 0.5
70 68 11 0.0 0.0 0.5
70 68 12 0.0 0.0 0.5
70 68 13 0

71 12 12 0.0 0.0 0.5
71 12 13 0.0 0.0 0.5
71 12 14 0.0 0.0 0.5
71 12 15 0.0 0.0 0.5
71 12 16 0.0 0.0 0.5
71 12 17 0.0 0.0 0.5
71 12 18 0.0 0.0 0.5
71 12 19 0.0 0.0 0.5
71 12 20 0.0 0.0 0.5
71 12 21 0.0 0.0 0.5
71 12 22 0.0 0.0 0.5
71 12 23 0.0 0.0 0.5
71 12 24 0.0 0.0 0.5
71 12 25 0.0 0.0 0.5
71 13 1 0.0 0.0 0.5
71 13 2 0.0 0.0 0.5
71 13 3 0.0 0.0 0.5
71 13 4 0.0 0.0 0.5
71 13 5 0.0 0.0 0.5
71 13 6 0.0 0.0 0.5
71 13 7 0.0 0.0 0.5
71 13 8 0.0 0.0 0.5
71 13 9 0.0 0.0 0.5
71 13 10 0.0 0.0 0.5
71 13 11 0.0 0.0 0.5
71 13 12 0.0 0.0 0.5
71 13 13 0.0 0.0 0.5
71 13 14 0.0 0.0 0.5
71 13 15 0.0 0.0 0.5
71 13 16 0.0 0.0 0.5
71 13 17 0.0 0.0 0.5
71 13 18 0.0 0.0 0.5
71 13 19 0.0 0.0 0.5
71 13 20 0.0 0.0 0.5
71 13 21 0.0 0.0 0.5
71 13 22 0.0 0.0 0.5
71 13 23 0.0 0.0 0.5
71 13 24 0.0 0.0 0.5
71 13 25 0.0 0.0 0.5
71 14 1 0.0 0.0 0.5
71 14 2 0.0 0.0 0.5
71 14 3 0.0 0.0 0.5
71 14 4 0.0 0.0 0.5
71 14 5 0.0 0.0 0.5
71 14 6 0.0 0.0 0.5
71 14 7 0.0 0.0 0.5
71 14 8 0.0 0.0 0.5
71 14 9 0.0 0.0 0.5
71 14 10 0

71 29 11 0.0 0.0 0.5
71 29 12 0.0 0.0 0.5
71 29 13 0.0 0.0 0.5
71 29 14 0.0 0.0 0.5
71 29 15 0.0 0.0 0.5
71 29 16 0.0 0.0 0.5
71 29 17 0.0 0.0 0.5
71 29 18 0.0 0.0 0.5
71 29 19 0.0 0.0 0.5
71 29 20 0.0 0.0 0.5
71 29 21 0.0 0.0 0.5
71 29 22 0.0 0.0 0.5
71 29 23 0.0 0.0 0.5
71 29 24 0.0 0.0 0.5
71 29 25 0.0 0.0 0.5
71 30 1 0.0 0.0 0.5
71 30 2 0.0 -0.2560506197771588 0.5
71 30 3 0.0 -0.4119876598332175 0.5
71 30 4 0.0 -0.440673101595007 0.5
71 30 5 0.0 -0.3419364359861592 0.5
71 30 6 0.0 -0.1494177732798165 0.5
71 30 7 0.0 0.0310172409920182 0.5
71 30 8 0.0 0.1762724693877551 0.5
71 30 9 0.0 0.2830453614730879 0.5
71 30 10 0.0 0.3358327695356738 0.5
71 30 11 0.0 0.3761453752122241 0.5
71 30 12 0.0 0.3952758257918551 0.5
71 30 13 0.0 0.3846420152628604 0.5
71 30 14 0.0 0.2816177406779661 0.5
71 30 15 0.0 0.2063848933408578 0.5
71 30 16 0.0 0.1303565567080045 0.5
71 30 17 0.0 0.0024759193918918 0.5
71 30 18 0.0 -0.081082972804054 0.5
71 30 19 0.0 -0.1176006815878378 0.5
71 30 20 0.0 -0.1470

71 40 15 0.0 -0.2098226393905191 0.5
71 40 16 0.0 -0.2226719036076663 0.5
71 40 17 0.0 -0.2315507043918919 0.5
71 40 18 0.0 -0.2337251216216216 0.5
71 40 19 0.0 -0.2142138192567567 0.5
71 40 20 0.0 -0.1829416756756756 0.5
71 40 21 0.0 -0.1508091490255376 0.5
71 40 22 0.0 -0.1150538073195187 0.5
71 40 23 0.0 0.0 0.5
71 40 24 0.0 0.0 0.5
71 40 25 0.0 0.0 0.5
71 41 1 0.0 0.0 0.5
71 41 2 0.0 0.0 0.5
71 41 3 0.0 0.0 0.5
71 41 4 0.0 0.0 0.5
71 41 5 0.0 0.0 0.5
71 41 6 0.0 0.0 0.5
71 41 7 0.0 0.0 0.5
71 41 8 0.0 0.0 0.5
71 41 9 0.0 0.0 0.5
71 41 10 0.0 0.0 0.5
71 41 11 0.0 0.0 0.5
71 41 12 0.0 0.0 0.5
71 41 13 0.0 0.0 0.5
71 41 14 0.0 0.0 0.5
71 41 15 0.0 0.0 0.5
71 41 16 0.0 0.0 0.5
71 41 17 0.0 0.0 0.5
71 41 18 0.0 0.0 0.5
71 41 19 0.0 0.0 0.5
71 41 20 0.0 0.0 0.5
71 41 21 0.0 0.0 0.5
71 41 22 0.0 0.0 0.5
71 41 23 0.0 0.0 0.5
71 41 24 0.0 0.0 0.5
71 41 25 0.0 0.0 0.5
71 42 1 0.0 0.0 0.5
71 42 2 0.0 0.0 0.5
71 42 3 0.0 0.0 0.5
71 42 4 0.0 0.0 0.5
71 42 5 0.0 0.0 0.5
71 42 6 0.0 0.0 0.5
71 42

71 56 7 0.0 0.0 0.5
71 56 8 0.0 0.0 0.5
71 56 9 0.0 0.0 0.5
71 56 10 0.0 0.0 0.5
71 56 11 0.0 0.0 0.5
71 56 12 0.0 0.0 0.5
71 56 13 0.0 0.0 0.5
71 56 14 0.0 0.0 0.5
71 56 15 0.0 0.0 0.5
71 56 16 0.0 0.0 0.5
71 56 17 0.0 0.0 0.5
71 56 18 0.0 0.0 0.5
71 56 19 0.0 0.0 0.5
71 56 20 0.0 0.0 0.5
71 56 21 0.0 0.0 0.5
71 56 22 0.0 0.0 0.5
71 56 23 0.0 0.0 0.5
71 56 24 0.0 0.0 0.5
71 56 25 0.0 0.0 0.5
71 57 1 0.0 0.0 0.5
71 57 2 0.0 0.0 0.5
71 57 3 0.0 0.0 0.5
71 57 4 0.0 0.0 0.5
71 57 5 0.0 0.0 0.5
71 57 6 0.0 0.0 0.5
71 57 7 0.0 0.0 0.5
71 57 8 0.0 0.0 0.5
71 57 9 0.0 0.0 0.5
71 57 10 0.0 0.0 0.5
71 57 11 0.0 0.0 0.5
71 57 12 0.0 0.0 0.5
71 57 13 0.0 0.0 0.5
71 57 14 0.0 0.0 0.5
71 57 15 0.0 0.0 0.5
71 57 16 0.0 0.0 0.5
71 57 17 0.0 0.0 0.5
71 57 18 0.0 0.0 0.5
71 57 19 0.0 0.0 0.5
71 57 20 0.0 0.0 0.5
71 57 21 0.0 0.0 0.5
71 57 22 0.0 0.0 0.5
71 57 23 0.0 0.0 0.5
71 57 24 0.0 0.0 0.5
71 57 25 0.0 0.0 0.5
71 58 1 0.0 0.0 0.5
71 58 2 0.0 0.0 0.5
71 58 3 0.0 0.0 0.5
71 58 4 0.0 0.0 0.5
71 58 5 

## 8. Calculate average semblance of checkerboards shifted in 3D

In [164]:
df_1=pd.read_csv("../check20_20_8/semblance_synth001_avgnd_r1_neu_p.dat",sep="\s+",header=None)
df_2=pd.read_csv("../check20_20_8/semblance_synth001_avgnd_r2_xpos_p.dat",sep="\s+",header=None)
df_3=pd.read_csv("../check20_20_8/semblance_synth001_avgnd_r3_xneg_p.dat",sep="\s+",header=None)
df_4=pd.read_csv("../check20_20_8/semblance_synth001_avgnd_r4_ypos_p.dat",sep="\s+",header=None)
df_5=pd.read_csv("../check20_20_8/semblance_synth001_avgnd_r5_yneg_p.dat",sep="\s+",header=None)
df_6=pd.read_csv("../check20_20_8/semblance_synth001_avgnd_r6_zdown_p.dat",sep="\s+",header=None)
df_7=pd.read_csv("../check20_20_8/semblance_synth001_avgnd_r7_zup_p.dat",sep="\s+",header=None)

avgsem=(df_1[5]+df_2[5]+df_3[5]+df_4[5]+df_5[5]+df_6[5]+df_7[5])/7.0
print(avgsem)
df_comb = df_1[[0,1,2,3]].copy()
df_comb[4]=avgsem
df_comb.to_csv("../check20_20_8/semblance_avgnd_average_chk20_p.dat",sep=" ",index=False, header=False)

0         0.5
1         0.5
2         0.5
3         0.5
4         0.5
         ... 
126020    0.5
126021    0.5
126022    0.5
126023    0.5
126024    0.5
Name: 5, Length: 126025, dtype: float64


In [166]:
fo=open("../check20_20_8/semblance_avgnd_average_chk20_comb.dat",'w')
df_1=pd.read_csv("../check20_20_8/semblance_avgnd_average_chk20_p.dat",sep="\s+",header=None)
df_2=pd.read_csv("../check20_20_8/semblance_avgnd_average_chk20_s.dat",sep="\s+",header=None)
#print(df_1)
#print(df_2)
for i in range(len(df_1[0])):
    print(df_1[0][i],df_1[1][i],df_1[2][i],min(df_1[4][i],df_2[4][i]),file=fo)

## 9. Nodes to coordinate transformation for semblance:

In [168]:
#Nodes to coordinates for semblance
lat0=-26.7
lon0=-67.1
dep0=-4.0

df_sem = pd.read_csv("../check20_20_8/semblance_avgnd_average_chk20_comb.dat",sep="\s+",header=None)
a1=4.0/110.574
a2=4.0/(111.320*cos(lat0*pi/180))

lonlist=round((lon0+(df_sem[0]-36)*a2),4)
latlist=round((lat0+(df_sem[1]-36)*a1),4)
deplist=(dep0+df_sem[2]-1)

# initialize data of lists.
data = {0: lonlist,1: latlist,2:deplist,3:df_sem[3]}  
# Create DataFrame
df = pd.DataFrame(data)
print(df)
df.to_csv("../check20_20_8/semblance_average_chk20_coord_comb.dat",sep=" ",index=False,header=None)

              0        1     2    3
0      -68.5077 -27.9661  -4.0  0.5
1      -68.5077 -27.9661  -3.0  0.5
2      -68.5077 -27.9661  -2.0  0.5
3      -68.5077 -27.9661  -1.0  0.5
4      -68.5077 -27.9661   0.0  0.5
...         ...      ...   ...  ...
126020 -65.6923 -25.4339  16.0  0.5
126021 -65.6923 -25.4339  17.0  0.5
126022 -65.6923 -25.4339  18.0  0.5
126023 -65.6923 -25.4339  19.0  0.5
126024 -65.6923 -25.4339  20.0  0.5

[126025 rows x 4 columns]
